In [66]:
import drawsvg as draw
import random
from pprint import pprint, pformat
import math

class Extent():
    
    def __init__(self, x=0, y=0, w=0, h=0):
        self.x = x
        self.y = y
        self.w = w
        self.h = h
        
    def __repr__(self):
        return f"{self.x},{self.y},{self.w},{self.h}"
        
    def __iter__(self):
        yield (self.x, self.y, self.w, self.h)
    
    def arc(self, drawing, n_points=40, radius=50, x0=0, y0=0, w=200, h=200, quadrant=0, edges=0, **line_config):
        points = []
        for i in range(n_points+1):
            theta = i*90./float(n_points)+90.*quadrant
            theta = math.radians(theta)
            x = radius * math.cos(theta) + x0
            y = radius * math.sin(theta) + y0
            
            match quadrant:
                case 1:
                    x += w
                case 2:
                    x += w
                    y += h
                case 3:
                    y += h
            points.extend((x,y))
        drawing.append( draw.Lines(*points, **line_config))
        
        clip_radius=w
        
        if edges > 1:
            # is corner
            clip_radius = w*2
        
        points=[]
        for i in range(n_points+1):
            theta = i*90./float(n_points)+90.*(quadrant+2)
            theta = math.radians(theta)
            x = radius * math.cos(theta) + x0
            y = radius * math.sin(theta) + y0
            match quadrant:
                case 0:
                    x += w
                    y += h
                    r = math.sqrt((x0-x)**2 + (y0-y)**2)
                case 1:
                    y += h
                    r = math.sqrt((x0+w-x)**2 + (y0-y)**2)
                case 2:
                    r = math.sqrt((x0+w-x)**2 + (y0+h-y)**2)
                case 3:
                    x += w
                    r = math.sqrt((x0-x)**2 + (y0+h-y)**2)
            if r > clip_radius:
                points.extend((x,y))
            else:
                if points:
                    drawing.append(draw.Lines(*points, **line_config))
                points = []
        if points:
            drawing.append(draw.Lines(*points, **line_config))


        
    def block(self, drawing, n_points=40, radius=50, x0=0, y0=0, w=200, h=200, quadrant=0, depth=1, edges=0, **line_config):

        # triangle
        # points = []
        # points.extend((x0,y0))
        # points.extend((x0,y0+h))
        # points.extend((x0+w,y0+h))
        # points.extend((x0+w,y0))
        # points.extend((x0,y0))
        # drawing.append( draw.Lines(*points, **line_config))
        
        spacing = 5
        n_circles = int(w/spacing)
        for i in range(0,n_circles+1):
            radius = spacing * i
            self.arc(
                drawing=drawing,
                n_points=40,
                x0=x0, 
                y0=y0, 
                w=w, 
                h=h,
                quadrant=quadrant,
                radius=radius,
                edges=edges,
                **line_config
            )
            
    def draw(self, drawing, depth=1, quadrant=0, edges=0, **config):
        # rect = draw.Rectangle(
        #     self.x, 
        #     self.y, 
        #     self.w, 
        #     self.h,
        #     **config)
        # drawing.append(rect)
        self.block(
            drawing=drawing,
            n_points=40,
            x0=self.x, 
            y0=self.y, 
            w=self.w, 
            h=self.h,
            quadrant=quadrant,
            depth=depth,
            edges=edges,
            **config)
        
    
    @property
    def x_mid(self):
        return self.w / 2 + self.x
    
    @property
    def y_mid(self):
        return self.h / 2 + self.y
        
        
"""
(0,200) (50,200) (100,200) (150,200) (200,200)
(0,150) (50,150) (100,150) (150,150) (200,150)
(0,100) (50,100) (100,100) (150,100) (200,100)
(0,50 ) (50,50 ) (100,50 ) (150,50 ) (200,50 )
(0,0  ) (50,0  ) (100,0. ) (150,0  ) (200,0. )
"""

class VisualQuadTree():

    def __init__(
        self, 
        top_left=None, 
        top_right=None, 
        bot_left=None,
        bot_right=None, 
        extent=None, 
        depth=0,
        max_depth=3,
        root_extent=None):
        
        self.extent = extent
        self.depth = depth
        self.max_depth = max_depth
        self.root_extent = root_extent
        
        if depth == 0:
            self.root_extent = self.extent
        
        if self.depth < max_depth:
            
            e = extent
            
            threshold = self.depth/float(self.max_depth)
            
            top_left_extent  = Extent(e.x, e.y_mid, e.w/2, e.h/2)
            top_right_extent = Extent(e.x_mid, e.y_mid, e.w/2, e.h/2)
            bot_left_extent  = Extent(e.x, e.y, e.w/2, e.h/2)
            bot_right_extent = Extent(e.x_mid, e.y, e.w/2, e.h/2)
            
            self.top_left    = VisualQuadTree(extent=top_left_extent, depth=self.depth+1, max_depth=self.max_depth, root_extent=self.root_extent)
            self.top_right   = VisualQuadTree(extent=top_right_extent, depth=self.depth+1, max_depth=self.max_depth, root_extent=self.root_extent)
            self.bot_left    = VisualQuadTree(extent=bot_left_extent, depth=self.depth+1, max_depth=self.max_depth, root_extent=self.root_extent)
            self.bot_right   = VisualQuadTree(extent=bot_right_extent, depth=self.depth+1, max_depth=self.max_depth, root_extent=self.root_extent)
            
        else:
            self.top_left  = None
            self.top_right = None
            self.bot_left  = None
            self.bot_right = None

    def draw(self, drawing, **config):
        default_config = dict(
                # stroke=["red", "green", "purple", "orange", "blue", "teal", "yellow", "magenta"][self.depth],
                stroke="blue",
                stroke_width=1,
                fill_opacity=0,
        )
        for key, value in default_config.items():
            if key not in config:
                config[key] = value
        # if self.top_right == None:
        #     return
        if self.depth == self.max_depth:
            from copy import deepcopy
            new_config = deepcopy(config)
            quadrant = random.choice([0,1,2,3])
            # detect edges
            edges = 0
            if self.extent.x == self.root_extent.x:
                new_config["stroke"] = "cyan"
                edges += 1
                if self.extent.y >= self.root_extent.h/2:
                    quadrant = 1
                else:
                    quadrant = 2
            if self.extent.y == self.root_extent.y:
                new_config["stroke"] = "magenta"
                edges += 1
                if self.extent.x >= self.root_extent.w / 2:
                    quadrant = 3
                else:
                    quadrant = 2
            if self.extent.x+self.extent.w == self.root_extent.w:
                new_config["stroke"] = "yellow"
                edges += 1
                if self.extent.y >= self.root_extent.h/2:
                    quadrant = 0
                else:
                    quadrant = 3
            if self.extent.y+self.extent.h == self.root_extent.h:
                new_config["stroke"] = "black"
                edges += 1
                if self.extent.x >= self.root_extent.w / 2:
                    quadrant = 0
                else:
                    quadrant = 1
            if edges < 2:
                quadrant = random.choice([0,1,2,3])
            self.extent.draw(drawing, depth=self.depth, quadrant=quadrant, edges=edges, **new_config)
        for quad_name, quadrant in {
            "tl":self.top_left, 
            "tr":self.top_right, 
            "bl":self.bot_left,
            "br":self.bot_right, 
        }.items():
            if quadrant != None:
                quadrant.draw(drawing, **config)
    
    def merge(self, special_quadrant="top_left"):
        
        for quad_name, quadrant in {
            "top_left":self.top_left, 
            "top_right":self.top_right, 
            "bot_left":self.bot_left,
            "bot_right":self.bot_right, 
        }.items():
            if quadrant != None:
                if quad_name == special_quadrant:
                    self.__setattr__(
                        quad_name, 
                        VisualQuadTree(
                            extent=quadrant.extent, 
                            depth=self.depth+1,
                            max_depth=self.depth+1, 
                            root_extent=self.root_extent))
                else:
                    quadrant.merge(special_quadrant)
                
    def to_dict(self):
        result = {}
        for k,v in self.__dict__.items():
            if isinstance(v, self.__class__):
                result[k] = v.to_dict() or v.extent
            if k == "extent":
                result[k] = v
        return result
        

block_size=100
drawing = draw.Drawing(block_size*8, block_size*8, origin=(0,0), displayInline=False)

extent = Extent(0, 0, int(drawing.width/2), int(drawing.height/2))
tree = VisualQuadTree(extent=extent, max_depth=4)
tree.merge("bot_left")
tree.draw(drawing, **{"stroke":"red"})

extent = Extent(int(drawing.width/2), 0, int(drawing.width/2), int(drawing.height/2))
tree = VisualQuadTree(extent=extent, max_depth=4)
tree.merge("bot_right")
tree.draw(drawing, **{"stroke":"green"})

extent = Extent(int(drawing.width/2), int(drawing.height/2), int(drawing.width/2), int(drawing.height/2))
tree = VisualQuadTree(extent=extent, max_depth=4)
tree.merge("top_right")
tree.draw(drawing, **{"stroke":"blue"})

extent = Extent(0, int(drawing.height/2), int(drawing.width/2), int(drawing.height/2))
tree = VisualQuadTree(extent=extent, max_depth=4)
tree.merge("top_left")
tree.draw(drawing, **{"stroke":"orange"})

drawing.save_png("quadtree_parquet_4.png")
drawing.save_svg("quadtree_parquet_4.svg")
drawing